# Learning linkset correctness

**Research Questions**: 
- can we train a neural network distingushing between correct and uncorrect links?
- can we train a neural network distingushing between a exactMatch and a closeMatch?



## Preparing the training sets
The training set is based on a set of linksets that have been generated building [Linked Thesaurus fRamework for Environment (LusTRE)](http://linkeddata.ge.imati.cnr.it/) as part of the research activity carried out during two EU funded projects: NatureSDIPlus and eENVplus. 


The procedure adopted to prepare a view of the linksets with the label, BT,NT,RT are described in 
* [Preparing Linkset involving local dumps](http://localhost:8888/notebooks/ai-related/LinkCorrectess/PreparingLinksetWithLocalDumps.ipynb)
, which include all the linksets not involving DBPEDIA
* [Preparing Linkset involving Dbpedia](http://localhost:8888/notebooks/ai-related/LinkCorrectess/PreparingLinksetWithDBPEDIA.ipynb)

### Useful tutorial 
 -  A  useful tutorial about pandas's dataframe is available at https://data36.com/pandas-tutorial-1-basics-reading-data-files-dataframes-data-selection/
 - creating and editing https://www.shanelynn.ie/using-pandas-dataframe-creating-editing-viewing-data-in-python/
 - [Advanced Jupyter Notebook Tricks — Part I](https://blog.dominodatalab.com/lesser-known-ways-of-using-notebooks/)

### Global variable 

In [25]:
### Global variables 
path="data/" # path where to find data
#namesa=['sBT','sprefLabel','sURI','oURI','oprefLabel','oBT', 'KindOfLink'] #column names for training data frame

## What features are we going to consider to characterize a link?


Text and Conceptual similarity among prefered labels  and  broader terms are considered as significant features on which classify a link.

Different approaches are available in order to work out the text similarity

### word2Vec
- A pretrained model for text similarity http://mccormickml.com/2016/04/12/googles-pretrained-word2vec-model-in-python/ (**pretrained model in Users/bubu/model/ but instructions outdated** )
- example of usage in  https://radimrehurek.com/gensim/models/keyedvectors.html
Others  resources 
- https://medium.freecodecamp.org/how-to-get-started-with-word2vec-and-then-how-to-make-it-work-d0a2fca9dad3
- https://www.slideshare.net/lechatpito
- https://code.google.com/archive/p/word2vec/
- [Vector Representations of Words IN TF](https://www.tensorflow.org/tutorials/representation/word2vec)
- [Stanford courser - Word Vector Representations: word2vec](https://www.youtube.com/watch?v=ERibwqs9p38)
- using word2Vec in rapidMiner https://community.rapidminer.com/discussion/43860/synonym-detection-with-word2vec
 -https://www.neuralmarkettrends.com/word2vec-example-process-rapidminer

### Glo Ve

- https://medium.com/@japneet121/word-vectorization-using-glove-76919685ee0b

### Text Similarity
- Basic text similarities https://pypi.org/project/textdistance/



# A - Attempt 1: Let's initialize the Word2Vec with a pre-existing model

## Design choices
- **design choice 1**: We use the Google’s pre-trained model see [here](http://mccormickml.com/2016/04/12/googles-pretrained-word2vec-model-in-python/). It’s 1.5GB! It includes word vectors for a vocabulary of 3 million words and phrases that they trained on roughly 100 billion words from a Google News dataset. The vector length is 300 features.
- **design choice 2**: Similarity(s1,s2) implements a first attempt to work out the similarity between two set of words. It works out the max of sim on the pairs taken in the cardinal product of the sets, not considering the stoplist. 





In [29]:
#It takes very long to be executed
# https://radimrehurek.com/gensim/models/keyedvectors.html
from gensim.models import Word2Vec
from gensim.models import KeyedVectors

#model = Word2Vec(common_texts, size=100, window=5, min_count=1, workers=4)
#word_vectors = model.wv
word_vectors = KeyedVectors.load_word2vec_format("/Users/bubu/model/GoogleNews-vectors-negative300.bin", binary=True)  # C bin format
 

## A1 - How to call the similarity between vectors

In [83]:
#similarity = word_vectors.similarity('africa'.lower(), 'Countries in Africa'.lower().split())
#print(similarity)
docdistance=word_vectors.wmdistance('africa', 'Africa')
print(docdistance)

0.675937254097414


In [84]:
#v= ['woman','man', 'house', 'pippo']
def printifvector(v):
    for e in v:
        print(e +":")
        try:
        #vector = word_vectors.wv.word_vec( word_vectors.doesnt_match(e), use_norm=True)
            print(word_vectors.get_vector(e)) 
        except KeyError as ex:
            print('exception for ' +e)


## A2 - Procedure  work to out similarity on BT according to the first attempt 


In [85]:
# Attempt to work out similarity between two set of words
#lw1 and lw2 are two documents containing set of words
def similarityBetweenSetsSplitingInWords(s1,s2):
    ## remove common words and not indexed words and tokenize
    stoplist = set('for a of the and to in'.split())
    if (type(s1) is not str) or (type(s2) is not str):
        return 0.0
    # tokenize and removing |
    remove= lambda x :x.replace('|',"")
    lw1=list(map(remove, s1.lower().split()))
    lw2=list(map(remove,s2.lower().split()))
    
    strip= lambda x :x.strip()
    lw1=list(map(strip, lw1))
    lw2=list(map(strip, lw2))
    
    
    
    ## what words are indexed?
    lw1 =  [word for word in lw1 if word not in stoplist]
    lw2 =  [word for word in lw2 if word not in stoplist]
    
    print(lw1)
    print(lw2)
    amax=-1.0
    
    # if one of the sets is empty it returns 0
    if not ((len(lw1) == 0) or (len(lw2) == 0)): 
        for i in lw1 :  
            lmax=-1.0
            try:
                #test if i is indexed otherwise exception
                word_vectors.get_vector(i) 
            except KeyError as ex:
                print('exception for ' +i)
                continue
            for ii in lw2 :
                try:
                     #test if i is indexed otherwise exception
                    word_vectors.get_vector(ii)
                except KeyError as ex:
                    print('exception for ' +ii)
                    continue
                sim=word_vectors.similarity(i,ii)
                #print('sim(%s, %s) = %f' %(i,ii,sim) )   
                lmax = max(sim , lmax)
                amax+=lmax
                       
    return amax



In [86]:
print(similarityBetweenSetsSplitingInWords("africa", 'africa'))


['africa']
['africa']
0.0


## maxInSplitWords (M)
Given 
*  two sets of words $S_1$ and $S_2$
*  a similarity functions
*  $(x_i,y_j) \in S_1 \times S_2$
  
maxInSplitWords implements the following mathematical function

$\text{maxInSplitWords(x,y,sim)}=\text{MAX}_{i,j}(sim(x_i,y_j))$

In [87]:
# Attempt to work out similarity between two set of words
# lw1 and lw2 are two documents containing set of words
# function is the similarity function to apply
# it returns the maximun similarity comaring the set product
def maxInSplitWords(s1,s2, function):
    ## remove common words and not indexed words and tokenize
    stoplist = set('for a of the and to in'.split())
    if (type(s1) is not str) or (type(s2) is not str):
        return 0.0
    # tokenize and removing |
    remove= lambda x :x.replace('|',"")
    lw1=list(map(remove, s1.lower().split()))
    lw2=list(map(remove,s2.lower().split()))
    
    strip= lambda x :x.strip()
    lw1=list(map(strip, lw1))
    lw2=list(map(strip, lw2))
    
    
    ## what words are indexed?
    lw1 =  [word for word in lw1 if word not in stoplist]
    lw2 =  [word for word in lw2 if word not in stoplist]
    
    print(lw1)
    print(lw2)
    lmax=float('nan')
    firstTime = True
    # if one of the sets is empty it returns 0
    if not ((len(lw1) == 0) or (len(lw2) == 0)): 
        for i in lw1 :  
            for ii in lw2 :
                sim=function(i,ii)
                if ( math.isnan(lmax)) :
                    lmax=sim
                else:
                    lmax = max(sim , lmax)                     
    return lmax



## SummingMax (SM)

Given 
*  two sets of words $S_1$ and $S_2$
*  a similarity functions
*  $(x_i,y_j) \in S_1 \times S_2$
  
summingMax implements the following mathematical function


$\text{summingMax(x,y,sim)}=\sum_i{\text{MAX}_{i,j}(sim(x_i,y_j))}$

In [88]:
# Attempt to work out similarity between two set of words
# lw1 and lw2 are two documents containing set of words
# function is the similarity function to apply
import math
def summingMax(s1, s2, function):
    ## remove common words and not indexed words and tokenize
    stoplist = set('for a of the and to in'.split())
    if (type(s1) is not str) or (type(s2) is not str):
        return 0.0
    # tokenize and removing |
    remove= lambda x :x.replace('|',"")
    lw1=list(map(remove, s1.lower().split()))
    lw2=list(map(remove,s2.lower().split()))
    
    strip= lambda x :x.strip()
    lw1=list(map(strip, lw1))
    lw2=list(map(strip, lw2))
    
    
    
    ## what words are indexed?
    lw1 =  [word for word in lw1 if word not in stoplist]
    lw2 =  [word for word in lw2 if word not in stoplist]
    
    print(lw1)
    print(lw2)
   
    amax=float('nan')
    #firstTime = True
    # if one of the sets is empty it returns 0
    if not ((len(lw1) == 0) or (len(lw2) == 0)): 
        for i in lw1 :  
            lmax=float('nan')
            for ii in lw2 :
                sim=function(i,ii)
                if (math.isnan(lmax)) :
                    lmax=sim
                    #firstTime =False
                else:
                    lmax = max(sim , lmax)
            if (math.isnan(amax)):
                amax=lmax;
            else: 
                amax+=lmax;
    return amax



In [89]:
print(summingMax('', '', textdistance.hamming.normalized_similarity))


[]
[]
nan


### Generating the List of validated linksets

In [90]:
# https://dzone.com/articles/listing-a-directory-with-python
import os

TrainingFiles= filter(lambda x: x.endswith('EnrichedLinkeset.csv'),  os.listdir(path)) 
 
for file in TrainingFiles : 
    print(file)
       
    

Thist2AGROVOCEnrichedLinkeset.csv
Thist2EUROVOCEnrichedLinkeset.csv
ThIST2BpediaEnrichedLinkeset.csv
Thist2GEMETEnrichedLinkeset.csv


In [95]:
import pandas as pd

def workOutSim():
    TrainingFiles= filter(lambda x: x.endswith('EnrichedLinkeset.csv'),  os.listdir(path)) 
    for file in TrainingFiles: 
        print(file)
        lf=pd.read_csv(path+ file,delimiter=",")
        lf=lf.fillna('')
        
        #BT  
        df['BT_similaritySInW']=0.0 
        df['BT_wmdistance']=df['BT_Mwmdistance']= df['BT_SMwmdistance']= 0.0
        df['BT_nhammingSim']= df['BT_MnhammingSim']= df['BT_SMnhammingSim']= 0.0
        #Preferred Label
        df['PrefLabel_similaritySInW']=0.0 
        df['PrefLabel_wmdistance']=df['PrefLabel_Mwmdistance']= df['PrefLabel_SMwmdistance']= 0.0
        df['PrefLabel_nhammingSim']= df['PrefLabel_MnhammingSim']= df['PrefLabel_SMnhammingSim']= 0.0
         #NT
        df['RT_similaritySInW']=0.0 
        df['RT_wmdistance']=df['RT_Mwmdistance']= df['RT_SMwmdistance']= 0.0
        df['RT_nhammingSim']= df['RT_MnhammingSim']= df['RT_SMnhammingSim']= 0.0


        l = range(1, len(df))
        for i in l:
            if (df.sBT.iloc[i]!='') and (df.oBT.iloc[i]!=''):
                df['BT_similaritySInW'][i] =similarityBetweenSetsSplitingInWords(df.sBT[i], df.oBT[i])
                df['BT_wmdistance'][i]=word_vectors.wmdistance(df.sBT[i], df.oBT[i])
                df['BT_Mwmdistance'][i]= maxInSplitWords(df.sBT[i], df.oBT[i], word_vectors.wmdistance)
                df['BT_SMwmdistance'][i]= summingMax(df.sBT[i], df.oBT[i], word_vectors.wmdistance)
                df['BT_nhammingSim'][i]=textdistance.hamming.normalized_similarity(df.sBT[i], df.oBT[i])
                df['BT_MnhammingSim'][i]=maxInSplitWords(df.sBT[i], df.oBT[i],textdistance.hamming.normalized_similarity)
                df['BT_SMnhammingSim'][i] =summingMax(df.sBT[i], df.oBT[i],textdistance.hamming.normalized_similarity)

            if (df.sRT.iloc[i]!='') and (df.oRT.iloc[i]!=''):
                 df['RT_similaritySInW'][i] =similarityBetweenSetsSplitingInWords(df.sRT[i], df.oRT[i])
                 df['RT_wmdistance'][i]=word_vectors.wmdistance(df.sRT[i], df.oRT[i])
                 df['RT_Mwmdistance'][i]= maxInSplitWords(df.sRT[i], df.oRT[i], word_vectors.wmdistance)
                 df['RT_SMwmdistance'][i]= summingMax(df.sRT[i], df.oRT[i], word_vectors.wmdistance)
                 df['RT_nhammingSim'][i]=textdistance.hamming.normalized_similarity(df.sRT[i], df.oRT[i])
                 df['RT_MnhammingSim'][i]=maxInSplitWords(df.sRT[i], df.oRT[i],textdistance.hamming.normalized_similarity)
                 df['RT_SMnhammingSim'][i] =summingMax(df.sRT[i], df.oRT[i],textdistance.hamming.normalized_similarity)
                
            if (df.sPrefLabel.iloc[i]!='') and (df.oBT.iloc[i]!=''):
                df['PrefLabel_similaritySInW'][i] =similarityBetweenSetsSplitingInWords(df.sPrefLabel[i], df.oPrefLabel[i])
                df['PrefLabel_wmdistance'][i]=word_vectors.wmdistance(df.sPrefLabel[i], df.oPrefLabel[i])
                df['PrefLabel_Mwmdistance'][i]= maxInSplitWords(df.sPrefLabel[i], df.oPrefLabel[i], word_vectors.wmdistance)
                df['PrefLabel_SMwmdistance'][i]= summingMax(df.sPrefLabel[i], df.oPrefLabel[i], word_vectors.wmdistance)
                df['PrefLabel_nhammingSim'][i]=textdistance.hamming.normalized_similarity(df.sPrefLabel[i], df.oPrefLabel[i])
                df['PrefLabel_MnhammingSim'][i]=maxInSplitWords(df.sPrefLabel[i], df.oPrefLabel[i],textdistance.hamming.normalized_similarity)
                df['PrefLabel_SMnhammingSim'][i] =summingMax(df.sPrefLabel[i], df.oPrefLabel[i],textdistance.hamming.normalized_similarity)
            
        df.to_csv(path+file.replace('.csv','SimilarityResult.csv'), sep=';')



In [97]:
workOutSim()

Thist2AGROVOCEnrichedLinkeset.csv
['africa']
['countries', 'africa', 'landlocked', 'countries', 'west', 'african', 'countries', 'wikipedia', 'categories', 'named', 'after', 'countries', 'states', 'territories', 'established', '1960', 'republics']
exception for 1960


/Users/bubu/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/bubu/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


['africa']
['countries', 'africa', 'landlocked', 'countries', 'west', 'african', 'countries', 'wikipedia', 'categories', 'named', 'after', 'countries', 'states', 'territories', 'established', '1960', 'republics']


/Users/bubu/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:29: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/bubu/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:30: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/bubu/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:31: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


['africa']
['countries', 'africa', 'landlocked', 'countries', 'west', 'african', 'countries', 'wikipedia', 'categories', 'named', 'after', 'countries', 'states', 'territories', 'established', '1960', 'republics']
['africa']
['countries', 'africa', 'landlocked', 'countries', 'west', 'african', 'countries', 'wikipedia', 'categories', 'named', 'after', 'countries', 'states', 'territories', 'established', '1960', 'republics']
['africa']
['countries', 'africa', 'landlocked', 'countries', 'west', 'african', 'countries', 'wikipedia', 'categories', 'named', 'after', 'countries', 'states', 'territories', 'established', '1960', 'republics']


...

['popular', 'geology', 'current', 'research']
['years', 'births', 'by', 'year', 'deaths', 'by', 'year', 'years', 'music', 'films', 'by', 'year', 'history', 'years', 'film']
['news']
['news']
['news']
['news']
['news']
['news']
['news']
['news']
['news']
['news']
['paleontology', 'predation', 'nutrients', 'trophic', 'analysis', 'diet', 'metabolism']
['food', 'science', 'digestive', 'system']
['paleontology', 'predation', 'nutrients', 'trophic', 'analysis', 'diet', 'metabolism']
['food', 'science', 'digestive', 'system']
['paleontology', 'predation', 'nutrients', 'trophic', 'analysis', 'diet', 'metabolism']
['food', 'science', 'digestive', 'system']
['paleontology', 'predation', 'nutrients', 'trophic', 'analysis', 'diet', 'metabolism']
['food', 'science', 'digestive', 'system']
['paleontology', 'predation', 'nutrients', 'trophic', 'analysis', 'diet', 'metabolism']
['food', 'science', 'digestive', 'system']
['nutrition']
['nutrition']
['nutrition']
['nutrition']
['nutrition']
['nutrition'

['paleontology', 'bones']
['orthopedic', 'surgical', 'procedures']
['osteology']
['osteology']
['osteology']
['osteology']
['osteology']
['osteology']
['osteology']
['osteology']
['osteology']
['osteology']
['ozone']
['ozone']
['ozone']
['ozone']
['ozone']
['ozone']
['ozone']
['ozone']
['ozone']
['ozone']
['pakistan']
['pakistan']
['pakistan']
['pakistan']
['pakistan']
['pakistan']
['pakistan']
['pakistan']
['pakistan']
['pakistan']
['paleobiology']
['paleobiology']
['paleobiology']
['paleobiology']
['paleobiology']
['paleobiology']
['paleobiology']
['paleobiology']
['paleobiology']
['paleobiology']
['paleoclimatology']
['paleoclimatology']
['paleoclimatology']
['paleoclimatology']
['paleoclimatology']
['paleoclimatology']
['paleoclimatology']
['paleoclimatology']
['paleoclimatology']
['paleoclimatology']
['paleogeography']
['paleogeography']
exception for paleogeography
['paleogeography']
['paleogeography']
['paleogeography']
['paleogeography']
['paleogeography']
['paleogeography']
['

['quality']
['quality']
['quality']
['quality']
['quality']
['quality']
['collecting']
['collecting']
['collecting']
['collecting']
['collecting']
['collecting']
['collecting']
['collecting']
['collecting']
['collecting']
['radiation']
['radiation']
['radiation']
['radiation']
['radiation']
['radiation']
['radiation']
['radiation']
['radiation']
['radiation']
['radioactivity']
['radioactivity']
['radioactivity']
['radioactivity']
['radioactivity']
['radioactivity']
['radioactivity']
['radioactivity']
['radioactivity']
['radioactivity']
['hills', 'landform', 'description', 'alpine', 'environment', 'geomorphology', 'landforms', 'mesas', 'highlands']
['mountaineering', 'mountain', 'ranges', 'climbing', 'hills']
['hills', 'landform', 'description', 'alpine', 'environment', 'geomorphology', 'landforms', 'mesas', 'highlands']
['mountaineering', 'mountain', 'ranges', 'climbing', 'hills']
['hills', 'landform', 'description', 'alpine', 'environment', 'geomorphology', 'landforms', 'mesas', 'high

['systems']
['systems']
['systems']
['systems']
['systems']
['systems']
['systems']
['systems']
['systems']
['systems']
['companies']
['companies']
['companies']
['companies']
['companies']
['companies']
['companies']
['companies']
['companies']
['companies']
['solar', 'energy', 'solar', 'system', 'solar', 'cycles', 'solar', 'nebula', 'planetology', 'planets', 'solar', 'wind', 'moon', 'solar', 'activity']
['stars', 'galaxies']
exception for planetology
['solar', 'energy', 'solar', 'system', 'solar', 'cycles', 'solar', 'nebula', 'planetology', 'planets', 'solar', 'wind', 'moon', 'solar', 'activity']
['stars', 'galaxies']
['solar', 'energy', 'solar', 'system', 'solar', 'cycles', 'solar', 'nebula', 'planetology', 'planets', 'solar', 'wind', 'moon', 'solar', 'activity']
['stars', 'galaxies']
['solar', 'energy', 'solar', 'system', 'solar', 'cycles', 'solar', 'nebula', 'planetology', 'planets', 'solar', 'wind', 'moon', 'solar', 'activity']
['stars', 'galaxies']
['solar', 'energy', 'solar', '

['topology']
['topology']
['topology']
['topology']
['transport']
['transport']
['transport']
['transport']
['transport']
['transport']
['transport']
['transport']
['transport']
['transport']
['tundra']
['tundra']
['tundra']
['tundra']
['tundra']
['tundra']
['tundra']
['tundra']
['tundra']
['tundra']
['tungstates']
['tungstates']
exception for tungstates
['tungstates']
['tungstates']
['tungstates']
['tungstates']
['tungstates']
['tungstates']
['tungstates']
['tungstates']
['urbanization']
['urbanization']
['urbanization']
['urbanization']
['urbanization']
['urbanization']
['urbanization']
['urbanization']
['urbanization']
['urbanization']
['valleys']
['valleys']
['valleys']
['valleys']
['valleys']
['valleys']
['valleys']
['valleys']
['valleys']
['valleys']
['evaluation']
['evaluation']
['evaluation']
['evaluation']
['evaluation']
['evaluation']
['evaluation']
['evaluation']
['evaluation']
['evaluation']
['vanadates']
['vanadates']
exception for vanadates
['vanadates']
['vanadates']
['v

## Cleaning  SimilarityReusults

In [102]:
TrainingFiles= filter(lambda x: x.endswith('SimilarityResult.csv'),  os.listdir(path)) 
for file in TrainingFiles: 
    print(file)
    lf=pd.read_csv(path+ file,delimiter=";")
    lf.to_csv(path+file.replace('SimilarityResult.csv','SimilarityResultOld.csv'), sep=';')
    lf1=lf[['s','o','KindOfLink','sBT','sNT','sRT','sPrefLabel','sAltLabels','oPrefLabel','oDefinition','oAltLabels','oBT','oNT','oRT','RT_similaritySInW','RT_wmdistance', 'RT_Mwmdistance', 'RT_SMwmdistance','RT_nhammingSim','RT_MnhammingSim','RT_SMnhammingSim','BT_similaritySInW','BT_wmdistance','BT_Mwmdistance','BT_SMwmdistance','BT_nhammingSim','BT_MnhammingSim','BT_SMnhammingSim','PrefLabel_similaritySInW','PrefLabel_wmdistance','PrefLabel_Mwmdistance','PrefLabel_SMwmdistance','PrefLabel_nhammingSim','PrefLabel_MnhammingSim','PrefLabel_SMnhammingSim'
]]
    lf1.to_csv(path+file.replace('SimilarityResult.csv','SimilarityResult1.csv'), sep=';')
    
    

ThIST2BpediaEnrichedLinkesetSimilarityResult.csv
Thist2AGROVOCEnrichedLinkesetSimilarityResult.csv
Thist2GEMETEnrichedLinkesetSimilarityResult.csv
Thist2EUROVOCEnrichedLinkesetSimilarityResult.csv


# Do not execute !!!  ATTEMPS made for DBPEdia

### Reading a specific validated linkset (Thist2DBPEDIA_ok.csv)

In [27]:
#preparing a dictionary with  

for file in TrainingFiles : 
    print(file)
       

### Reading a specific validated linkset (Thist2DBPEDIA_ok.csv)

In [27]:
#preparing a dictionary with  

for file in TrainingFiles : 
    print(file)
       

In [28]:
import pandas as pd


# reading Thist2DBPEDIA_ok.csv
THIST2DBPEDIA_df=pd.read_csv(path+'ThIST2BpediaEnrichedLinkeset.csv',delimiter=",")
#deleting row 0 which contains the old colums name
#THIST2DBPEDIA_df=THIST2DBPEDIA_df.drop([0])
THIST2DBPEDIA_df['KindOfLink']=THIST2DBPEDIA_df['KindOfLink'].fillna('W')

THIST2DBPEDIA_df=THIST2DBPEDIA_df.fillna('')

#THIST2DBPEDIA_df.count()

#filter all the wrong Links
print('num wrong link',THIST2DBPEDIA_df[THIST2DBPEDIA_df['KindOfLink']=='W']['KindOfLink'].count())
print('num close link',THIST2DBPEDIA_df[THIST2DBPEDIA_df['KindOfLink']=='C']['KindOfLink'].count())
print('num exact link',THIST2DBPEDIA_df[THIST2DBPEDIA_df['KindOfLink']=='E']['KindOfLink'].count())




num wrong link 11
num close link 28
num exact link 933


In [37]:
a = 'africa'.lower().split()
b = 'countries in africa'.lower().split()
c ='countries in Europe'.lower().split()
d ='Italy'
similarity = word_vectors.wmdistance(a, b)
print("{:.4f}".format(similarity))
similarity = word_vectors.wmdistance(a, c)
print("{:.4f}".format(similarity))
similarity = word_vectors.wmdistance(b, c)
print("{:.4f}".format(similarity))
similarity = word_vectors.wmdistance(a, d)
print("{:.4f}".format(similarity))

#a='great africa'.lower().strip().split()
#b='Countries in Africa'.lower().strip().split()
#print(a)
#print(b)
#similarity = word_vectors.distances(a,b )
#print(similarity)
#docdistance=word_vectors.wmdistance('woman', 'man')
#print(docdistance)

2.6975
3.7890
1.0915
4.1048


In [73]:
import textdistance
#df  data frame
df=THIST2DBPEDIA_df.drop_duplicates()
##TEST
#df=THIST2DBPEDIA_df[THIST2DBPEDIA_df['sBT']=='']

df['BT_similaritySInW']=0.0 
df['BT_wmdistance']=df['BT_Mwmdistance']= df['BT_SMwmdistance']= 0.0
df['BT_nhammingSim']= df['BT_MnhammingSim']= df['BT_SMnhammingSim']= 0.0



l = range(1, len(df))
for i in l:
    if (df.sBT.iloc[i]!='') and (df.oBT.iloc[i]!=''):
        df['BT_similaritySInW'][i] =similarityBetweenSetsSplitingInWords(df.sBT[i], df.oBT[i])
        df['BT_wmdistance'][i]=word_vectors.wmdistance(df.sBT[i], df.oBT[i])
        df['BT_Mwmdistance'][i]= maxInSplitWords(df.sBT[i], df.oBT[i], word_vectors.wmdistance)
        df['BT_SMwmdistance'][i]= summingMax(df.sBT[i], df.oBT[i], word_vectors.wmdistance)
        df['BT_nhammingSim'][i]=textdistance.hamming.normalized_similarity(df.sBT[i], df.oBT[i])
        df['BT_MnhammingSim'][i]=maxInSplitWords(df.sBT[i], df.oBT[i],textdistance.hamming.normalized_similarity)
        df['BT_SMnhammingSim'][i] =summingMax(df.sBT[i], df.oBT[i],textdistance.hamming.normalized_similarity)


['africa']
['countries', 'africa', 'landlocked', 'countries', 'west', 'african', 'countries', 'wikipedia', 'categories', 'named', 'after', 'countries', 'states', 'territories', 'established', '1960', 'republics']
exception for 1960


/Users/bubu/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:16: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  app.launch_new_instance()
/Users/bubu/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


['africa']
['countries', 'africa', 'landlocked', 'countries', 'west', 'african', 'countries', 'wikipedia', 'categories', 'named', 'after', 'countries', 'states', 'territories', 'established', '1960', 'republics']


/Users/bubu/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:18: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/bubu/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/bubu/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


['africa']
['countries', 'africa', 'landlocked', 'countries', 'west', 'african', 'countries', 'wikipedia', 'categories', 'named', 'after', 'countries', 'states', 'territories', 'established', '1960', 'republics']
['africa']
['countries', 'africa', 'landlocked', 'countries', 'west', 'african', 'countries', 'wikipedia', 'categories', 'named', 'after', 'countries', 'states', 'territories', 'established', '1960', 'republics']


...

['trinidad', 'tobago']
['islands', 'trinidad', 'tobago', 'wikipedia', 'categories', 'named', 'after', 'islands']
['trinidad', 'tobago']
['islands', 'trinidad', 'tobago', 'wikipedia', 'categories', 'named', 'after', 'islands']
['tuscany', 'islands', 'europe', 'europa', 'island']
['wikipedia', 'categories', 'named', 'after', 'islands', 'province', 'livorno', 'islands', 'tuscany']
exception for tuscany
exception for livorno
exception for tuscany
exception for livorno
exception for tuscany
exception for livorno
exception for tuscany
exception for livorno
exception for tuscany
['tuscany', 'islands', 'europe', 'europa', 'island']
['wikipedia', 'categories', 'named', 'after', 'islands', 'province', 'livorno', 'islands', 'tuscany']
['tuscany', 'islands', 'europe', 'europa', 'island']
['wikipedia', 'categories', 'named', 'after', 'islands', 'province', 'livorno', 'islands', 'tuscany']
['tuscany', 'islands', 'europe', 'europa', 'island']
['wikipedia', 'categories', 'named', 'after', 'islands', '

['uzbekistan']
['cities', 'uzbekistan', 'wikipedia', 'categories', 'named', 'after', 'populated', 'places', 'uzbekistan', 'populated', 'places', 'tashkent', 'region', 'capitals', 'asia', 'wikipedia', 'categories', 'named', 'after', 'capitals']
['uzbekistan']
['cities', 'uzbekistan', 'wikipedia', 'categories', 'named', 'after', 'populated', 'places', 'uzbekistan', 'populated', 'places', 'tashkent', 'region', 'capitals', 'asia', 'wikipedia', 'categories', 'named', 'after', 'capitals']
['uzbekistan']
['cities', 'uzbekistan', 'wikipedia', 'categories', 'named', 'after', 'populated', 'places', 'uzbekistan', 'populated', 'places', 'tashkent', 'region', 'capitals', 'asia', 'wikipedia', 'categories', 'named', 'after', 'capitals']
['uzbekistan']
['cities', 'uzbekistan', 'wikipedia', 'categories', 'named', 'after', 'populated', 'places', 'uzbekistan', 'populated', 'places', 'tashkent', 'region', 'capitals', 'asia', 'wikipedia', 'categories', 'named', 'after', 'capitals']
['venezuela']
['wikipedi

['caribbean', 'region', 'greater', 'antilles', 'central', 'america', 'antilles', 'west', 'indies']
['island', 'countries', 'wikipedia', 'categories', 'named', 'after', 'islands', 'countries', 'caribbean', 'countries', 'north', 'america', 'member', 'states', 'commonwealth', 'nations', 'states', 'territories', 'established', '1962', 'english-speaking', 'countries', 'territories', 'wikipedia', 'categories', 'named', 'after', 'countries']
['caribbean', 'region', 'greater', 'antilles', 'central', 'america', 'antilles', 'west', 'indies']
['island', 'countries', 'wikipedia', 'categories', 'named', 'after', 'islands', 'countries', 'caribbean', 'countries', 'north', 'america', 'member', 'states', 'commonwealth', 'nations', 'states', 'territories', 'established', '1962', 'english-speaking', 'countries', 'territories', 'wikipedia', 'categories', 'named', 'after', 'countries']
['caribbean', 'region', 'greater', 'antilles', 'central', 'america', 'antilles', 'west', 'indies']
['island', 'countries',

['caribbean', 'region', 'lesser', 'antilles', 'central', 'america', 'antilles', 'west', 'indies']
['island', 'countries', 'countries', 'caribbean', 'countries', 'north', 'america', 'member', 'states', 'commonwealth', 'nations', 'english-speaking', 'countries', 'territories', 'wikipedia', 'categories', 'named', 'after', 'countries']
['caribbean', 'region', 'lesser', 'antilles', 'central', 'america', 'antilles', 'west', 'indies']
['island', 'countries', 'countries', 'caribbean', 'countries', 'north', 'america', 'member', 'states', 'commonwealth', 'nations', 'english-speaking', 'countries', 'territories', 'wikipedia', 'categories', 'named', 'after', 'countries']
['caribbean', 'region', 'lesser', 'antilles', 'central', 'america', 'antilles', 'west', 'indies']
['island', 'countries', 'countries', 'caribbean', 'countries', 'north', 'america', 'member', 'states', 'commonwealth', 'nations', 'english-speaking', 'countries', 'territories', 'wikipedia', 'categories', 'named', 'after', 'countries'

['greece']
['wikipedia', 'categories', 'named', 'after', 'islands', 'tourism', 'greece', 'wikipedia', 'categories', 'named', 'after', 'populated', 'places', 'greece', 'municipalities', 'ionian', 'islands', '(region)']
['greece']
['wikipedia', 'categories', 'named', 'after', 'islands', 'tourism', 'greece', 'wikipedia', 'categories', 'named', 'after', 'populated', 'places', 'greece', 'municipalities', 'ionian', 'islands', '(region)']
['greece']
['wikipedia', 'categories', 'named', 'after', 'islands', 'tourism', 'greece', 'wikipedia', 'categories', 'named', 'after', 'populated', 'places', 'greece', 'municipalities', 'ionian', 'islands', '(region)']
['greece']
['wikipedia', 'categories', 'named', 'after', 'islands', 'tourism', 'greece', 'wikipedia', 'categories', 'named', 'after', 'populated', 'places', 'greece', 'municipalities', 'ionian', 'islands', '(region)']


#### Printing the similaritities according to the Similarity 

In [71]:
#df['KindOfLink']=df['KindOfLink'].fillna('W')
df.head()


Unnamed: 0                                                  s  \
559         559  http://linkeddata.ge.imati.cnr.it/resource/ThI...   
560         560  http://linkeddata.ge.imati.cnr.it/resource/ThI...   
561         561  http://linkeddata.ge.imati.cnr.it/resource/ThI...   
562         562  http://linkeddata.ge.imati.cnr.it/resource/ThI...   
563         563  http://linkeddata.ge.imati.cnr.it/resource/ThI...   

                                                     o KindOfLink sBT sNT  \
559         http://dbpedia.org/resource/Category:Seams          C           
560         http://dbpedia.org/resource/Category:Tides          E           
561         http://dbpedia.org/resource/Category:Tides          C           
562  http://dbpedia.org/resource/Category:Transport...          E           
563  http://dbpedia.org/resource/Category:Ornamenta...          W           

                                                   sRT      sPrefLabel  \
559  mineral deposits| mining| stratiform deposits|...           seams   
560  ocean circulation| tidal currents| littoral er...           tides   
561  ocean circulation| tidal currents| littoral er...           tides   
562             subways| pipelines| sediment transport  transportation   
563                               paleontology| shells   ornamentation   

    sAltLabels      oPrefLabel  ...  \
559                      Seams  ...   
560                      Tides  ...   
561                      Tides  ...   
562             Transportation  ...   
563              Ornamentation  ...   

                                                   oBT oNT       oRT  \
559                                             Sewing                 
560  Geophysics| Moon| Physical oceanography| Tidal...                 
561  Geophysics| Moon| Physical oceanography| Tidal...                 
562                                                                    
563  Melody| Musical terminology| Musical technique...      Ornament   

    similaritySInW wmdistance  Mwmdistance  SMwmdistance  nhammingSim  \
559            0.0        0.0          0.0           0.0          0.0   
560            0.0        0.0          0.0           0.0          0.0   
561            0.0        0.0          0.0           0.0          0.0   
562            0.0        0.0          0.0           0.0          0.0   
563            0.0        0.0          0.0           0.0          0.0   

     MnhammingSim  SMnhammingSim  
559           0.0            0.0  
560           0.0            0.0  
561           0.0            0.0  
562           0.0            0.0  
563           0.0            0.0  

[5 rows x 22 columns]

In [75]:

#saving the results in Thist2DBPEDIA_ok_res.csv
df.to_csv(path+'Thist2DBPEDIA_ok_res.csv', sep=';') 

In [76]:
df['RT_similaritySInW']=0.0 
df['RT_wmdistance']=df['RT_Mwmdistance']= df['RT_SMwmdistance']= 0.0
df['RT_nhammingSim']= df['RT_MnhammingSim']= df['RT_SMnhammingSim']= 0.0

l = range(1, len(df))
for i in l:
    if (df.sRT.iloc[i]!='') and (df.oRT.iloc[i]!=''):
         df['RT_similaritySInW'][i] =similarityBetweenSetsSplitingInWords(df.sRT[i], df.oRT[i])
         df['RT_wmdistance'][i]=word_vectors.wmdistance(df.sRT[i], df.oRT[i])
         df['RT_Mwmdistance'][i]= maxInSplitWords(df.sRT[i], df.oRT[i], word_vectors.wmdistance)
         df['RT_SMwmdistance'][i]= summingMax(df.sRT[i], df.oRT[i], word_vectors.wmdistance)
         df['RT_nhammingSim'][i]=textdistance.hamming.normalized_similarity(df.sRT[i], df.oRT[i])
         df['RT_MnhammingSim'][i]=maxInSplitWords(df.sRT[i], df.oRT[i],textdistance.hamming.normalized_similarity)
         df['RT_SMnhammingSim'][i] =summingMax(df.sRT[i], df.oRT[i],textdistance.hamming.normalized_similarity)

['gulf', 'guinea', 'volta', 'river', 'volta', 'basin']
['guinea-bissau', 'equatorial', 'guinea', 'french', 'guiana', 'guyana', 'papua', 'new', 'guinea', 'new', 'guinea', 'guinea']
exception for guinea-bissau
exception for guiana
exception for guyana
exception for papua
exception for guinea-bissau
exception for guiana
exception for guyana
exception for papua
exception for guinea-bissau
exception for guiana
exception for guyana
exception for papua
exception for guinea-bissau
exception for guiana
exception for guyana
exception for papua
exception for guinea-bissau
exception for guiana
exception for guyana
exception for papua
exception for guinea-bissau
exception for guiana
exception for guyana
exception for papua


/Users/bubu/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  
/Users/bubu/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  if __name__ == '__main__':


['gulf', 'guinea', 'volta', 'river', 'volta', 'basin']
['guinea-bissau', 'equatorial', 'guinea', 'french', 'guiana', 'guyana', 'papua', 'new', 'guinea', 'new', 'guinea', 'guinea']


/Users/bubu/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  # Remove the CWD from sys.path while we load stuff.
/Users/bubu/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  # This is added back by InteractiveShellApp.init_path()
/Users/bubu/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  if sys.path[0] =

['gulf', 'guinea', 'volta', 'river', 'volta', 'basin']
['guinea-bissau', 'equatorial', 'guinea', 'french', 'guiana', 'guyana', 'papua', 'new', 'guinea', 'new', 'guinea', 'guinea']
['gulf', 'guinea', 'volta', 'river', 'volta', 'basin']
['guinea-bissau', 'equatorial', 'guinea', 'french', 'guiana', 'guyana', 'papua', 'new', 'guinea', 'new', 'guinea', 'guinea']
['gulf', 'guinea', 'volta', 'river', 'volta', 'basin']
['guinea-bissau', 'equatorial', 'guinea', 'french', 'guiana', 'guyana', 'papua', 'new', 'guinea', 'new', 'guinea', 'guinea']
['caucasus', 'azov', 'sea', 'ussr', 'urals']
['soviet', 'union']
exception for caucasus
exception for azov
exception for urals
['caucasus', 'azov', 'sea', 'ussr', 'urals']
['soviet', 'union']
['caucasus', 'azov', 'sea', 'ussr', 'urals']
['soviet', 'union']
['caucasus', 'azov', 'sea', 'ussr', 'urals']
['soviet', 'union']
['caucasus', 'azov', 'sea', 'ussr', 'urals']
['soviet', 'union']
['malaysia', 'brunei', 'indonesia', 'pacific', 'ocean']
['kalimantan']
ex

...

['passband', 'filters', 'wiener', 'filters', 'continuous', 'filters', 'geotextiles', 'recursive', 'filters', 'seismic', 'methods', 'dispersive', 'filters', 'multichannel', 'methods', 'adaptive', 'filters', 'numerical', 'filters', 'multichannel', 'filters', 'kalman', 'filters', 'elastic', 'waves', 'spatial', 'frequency', 'filters', 'analog', 'filters', 'discrete', 'filters', 'optimal', 'filters', 'deconvolution', 'signals', 'noise', 'distortion', 'seismology']
['signal', 'processing', 'filter', 'spam', 'filtering', 'anti-spam', 'optical', 'filters']
['passband', 'filters', 'wiener', 'filters', 'continuous', 'filters', 'geotextiles', 'recursive', 'filters', 'seismic', 'methods', 'dispersive', 'filters', 'multichannel', 'methods', 'adaptive', 'filters', 'numerical', 'filters', 'multichannel', 'filters', 'kalman', 'filters', 'elastic', 'waves', 'spatial', 'frequency', 'filters', 'analog', 'filters', 'discrete', 'filters', 'optimal', 'filters', 'deconvolution', 'signals', 'noise', 'distorti

['sewage', 'sludge', 'thermal', 'pollution', 'leaking', 'underground', 'storage', 'tanks', 'sulfuric', 'acid', 'toxic', 'materials', 'urban', 'geology', 'cyanides', 'water', 'treatment', 'metals', 'regulations', 'surface', 'water', 'waste', 'disposal', 'potability', 'hydrology', 'heavy', 'metals', 'urban', 'environment', 'pollutants', 'polluted', 'water', 'soil', 'gases', 'impurities', 'geochemistry', 'background', 'level', 'remediation', 'purification', 'environmental', 'monitoring', 'radioactive', 'waste', 'point', 'sources', 'industrial', 'waste', 'human', 'ecology', 'hydrocarbons', 'acid', 'mine', 'drainage', 'environmental', 'geology', 'medical', 'geology', 'waste', 'disposal', 'sites', 'sewers', 'geochemical', 'anomalies', 'conservation', 'oil', 'spills', 'geologic', 'hazards', 'dilution', 'decontamination', 'water', 'management', 'environmental', 'impact', 'evaluation', 'land', 'use', 'waste', 'water', 'reclamation', 'near-field', 'radioactivity', 'bioremediation', 'protected', 

['popular', 'geology', 'current', 'research']
['years', 'births', 'by', 'year', 'deaths', 'by', 'year', 'years', 'music', 'films', 'by', 'year', 'history', 'years', 'film']
['popular', 'geology', 'current', 'research']
['years', 'births', 'by', 'year', 'deaths', 'by', 'year', 'years', 'music', 'films', 'by', 'year', 'history', 'years', 'film']
['popular', 'geology', 'current', 'research']
['years', 'births', 'by', 'year', 'deaths', 'by', 'year', 'years', 'music', 'films', 'by', 'year', 'history', 'years', 'film']
['popular', 'geology', 'current', 'research']
['years', 'births', 'by', 'year', 'deaths', 'by', 'year', 'years', 'music', 'films', 'by', 'year', 'history', 'years', 'film']
['popular', 'geology', 'current', 'research']
['years', 'births', 'by', 'year', 'deaths', 'by', 'year', 'years', 'music', 'films', 'by', 'year', 'history', 'years', 'film']
['paleontology', 'predation', 'nutrients', 'trophic', 'analysis', 'diet', 'metabolism']
['food', 'science', 'digestive', 'system']
['pa

['crystal', 'structure']
['quasiregular', 'polyhedra', 'platonic', 'solids', 'archimedean', 'solids', 'images', 'polyhedra', 'tessellation', 'kepler–poinsot', 'polyhedra', 'prismatoid', 'polyhedra', 'uniform', 'polyhedra', 'catalan', 'solids', 'johnson', 'solids', 'pyramids', 'bipyramids']
['crystal', 'structure']
['quasiregular', 'polyhedra', 'platonic', 'solids', 'archimedean', 'solids', 'images', 'polyhedra', 'tessellation', 'kepler–poinsot', 'polyhedra', 'prismatoid', 'polyhedra', 'uniform', 'polyhedra', 'catalan', 'solids', 'johnson', 'solids', 'pyramids', 'bipyramids']
['runoff', 'atmospheric', 'precipitation', 'hydrology', 'crystallization', 'geochemistry', 'sedimentation', 'salt', 'water', 'watersheds', 'storms', 'water']
['clouds']
['runoff', 'atmospheric', 'precipitation', 'hydrology', 'crystallization', 'geochemistry', 'sedimentation', 'salt', 'water', 'watersheds', 'storms', 'water']
['clouds']
['runoff', 'atmospheric', 'precipitation', 'hydrology', 'crystallization', 'geoc

['bogs', 'marshes', 'lacustrine', 'features', 'shore', 'features', 'spartina', 'alterniflora', 'conservation', 'geomorphology', 'vegetation', 'wilderness', 'areas', 'grasslands', 'swamps', 'ecology', 'fluvial', 'features']
['landforms', 'bodies', 'water']
['bogs', 'marshes', 'lacustrine', 'features', 'shore', 'features', 'spartina', 'alterniflora', 'conservation', 'geomorphology', 'vegetation', 'wilderness', 'areas', 'grasslands', 'swamps', 'ecology', 'fluvial', 'features']
['landforms', 'bodies', 'water']
['autochthons', 'allochthons', 'structural', 'geology', 'tectonics', 'erosion', 'features', 'overthrust', 'faults']
['microsoft', 'windows']
exception for autochthons
exception for allochthons
['autochthons', 'allochthons', 'structural', 'geology', 'tectonics', 'erosion', 'features', 'overthrust', 'faults']
['microsoft', 'windows']
['autochthons', 'allochthons', 'structural', 'geology', 'tectonics', 'erosion', 'features', 'overthrust', 'faults']
['microsoft', 'windows']
['autochthons

In [76]:
def workSimilaritiesON(field, df):
    
    df[field+'_similaritySInW']=0.0 
    df[field+'_wmdistance']=df[field+'_Mwmdistance']= df[field+'_SMwmdistance']= 0.0
    df[field+'_nhammingSim']= df[field+'_MnhammingSim']= df[field+'_SMnhammingSim']= 0.0

    l = range(1, len(df))
    for i in l:
        if (df['s'+field].iloc[i]!='') and (df['o'+field].iloc[i]!=''):
             df[field+'_similaritySInW'][i] =similarityBetweenSetsSplitingInWords(df['s'+field][i], df.oRT[i])
             df[field+'_wmdistance'][i]=word_vectors.wmdistance(df.sRT[i], df.oRT[i])
             df[field+'_Mwmdistance'][i]= maxInSplitWords(df.sRT[i], df.oRT[i], word_vectors.wmdistance)
             df[field+'_SMwmdistance'][i]= summingMax(df.sRT[i], df.oRT[i], word_vectors.wmdistance)
             df[field+'_nhammingSim'][i]=textdistance.hamming.normalized_similarity(df.sRT[i], df.oRT[i])
             df[field+'_MnhammingSim'][i]=maxInSplitWords(df.sRT[i], df.oRT[i],textdistance.hamming.normalized_similarity)
             df[field+'_SMnhammingSim'][i] =summingMax(df.sRT[i], df.oRT[i],textdistance.hamming.normalized_similarity)

['gulf', 'guinea', 'volta', 'river', 'volta', 'basin']
['guinea-bissau', 'equatorial', 'guinea', 'french', 'guiana', 'guyana', 'papua', 'new', 'guinea', 'new', 'guinea', 'guinea']
exception for guinea-bissau
exception for guiana
exception for guyana
exception for papua
exception for guinea-bissau
exception for guiana
exception for guyana
exception for papua
exception for guinea-bissau
exception for guiana
exception for guyana
exception for papua
exception for guinea-bissau
exception for guiana
exception for guyana
exception for papua
exception for guinea-bissau
exception for guiana
exception for guyana
exception for papua
exception for guinea-bissau
exception for guiana
exception for guyana
exception for papua


/Users/bubu/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  
/Users/bubu/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  if __name__ == '__main__':


['gulf', 'guinea', 'volta', 'river', 'volta', 'basin']
['guinea-bissau', 'equatorial', 'guinea', 'french', 'guiana', 'guyana', 'papua', 'new', 'guinea', 'new', 'guinea', 'guinea']


/Users/bubu/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  # Remove the CWD from sys.path while we load stuff.
/Users/bubu/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  # This is added back by InteractiveShellApp.init_path()
/Users/bubu/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  if sys.path[0] =

['gulf', 'guinea', 'volta', 'river', 'volta', 'basin']
['guinea-bissau', 'equatorial', 'guinea', 'french', 'guiana', 'guyana', 'papua', 'new', 'guinea', 'new', 'guinea', 'guinea']
['gulf', 'guinea', 'volta', 'river', 'volta', 'basin']
['guinea-bissau', 'equatorial', 'guinea', 'french', 'guiana', 'guyana', 'papua', 'new', 'guinea', 'new', 'guinea', 'guinea']
['gulf', 'guinea', 'volta', 'river', 'volta', 'basin']
['guinea-bissau', 'equatorial', 'guinea', 'french', 'guiana', 'guyana', 'papua', 'new', 'guinea', 'new', 'guinea', 'guinea']
['caucasus', 'azov', 'sea', 'ussr', 'urals']
['soviet', 'union']
exception for caucasus
exception for azov
exception for urals
['caucasus', 'azov', 'sea', 'ussr', 'urals']
['soviet', 'union']
['caucasus', 'azov', 'sea', 'ussr', 'urals']
['soviet', 'union']
['caucasus', 'azov', 'sea', 'ussr', 'urals']
['soviet', 'union']
['caucasus', 'azov', 'sea', 'ussr', 'urals']
['soviet', 'union']
['malaysia', 'brunei', 'indonesia', 'pacific', 'ocean']
['kalimantan']
ex

...

['passband', 'filters', 'wiener', 'filters', 'continuous', 'filters', 'geotextiles', 'recursive', 'filters', 'seismic', 'methods', 'dispersive', 'filters', 'multichannel', 'methods', 'adaptive', 'filters', 'numerical', 'filters', 'multichannel', 'filters', 'kalman', 'filters', 'elastic', 'waves', 'spatial', 'frequency', 'filters', 'analog', 'filters', 'discrete', 'filters', 'optimal', 'filters', 'deconvolution', 'signals', 'noise', 'distortion', 'seismology']
['signal', 'processing', 'filter', 'spam', 'filtering', 'anti-spam', 'optical', 'filters']
['passband', 'filters', 'wiener', 'filters', 'continuous', 'filters', 'geotextiles', 'recursive', 'filters', 'seismic', 'methods', 'dispersive', 'filters', 'multichannel', 'methods', 'adaptive', 'filters', 'numerical', 'filters', 'multichannel', 'filters', 'kalman', 'filters', 'elastic', 'waves', 'spatial', 'frequency', 'filters', 'analog', 'filters', 'discrete', 'filters', 'optimal', 'filters', 'deconvolution', 'signals', 'noise', 'distorti

['sewage', 'sludge', 'thermal', 'pollution', 'leaking', 'underground', 'storage', 'tanks', 'sulfuric', 'acid', 'toxic', 'materials', 'urban', 'geology', 'cyanides', 'water', 'treatment', 'metals', 'regulations', 'surface', 'water', 'waste', 'disposal', 'potability', 'hydrology', 'heavy', 'metals', 'urban', 'environment', 'pollutants', 'polluted', 'water', 'soil', 'gases', 'impurities', 'geochemistry', 'background', 'level', 'remediation', 'purification', 'environmental', 'monitoring', 'radioactive', 'waste', 'point', 'sources', 'industrial', 'waste', 'human', 'ecology', 'hydrocarbons', 'acid', 'mine', 'drainage', 'environmental', 'geology', 'medical', 'geology', 'waste', 'disposal', 'sites', 'sewers', 'geochemical', 'anomalies', 'conservation', 'oil', 'spills', 'geologic', 'hazards', 'dilution', 'decontamination', 'water', 'management', 'environmental', 'impact', 'evaluation', 'land', 'use', 'waste', 'water', 'reclamation', 'near-field', 'radioactivity', 'bioremediation', 'protected', 

['popular', 'geology', 'current', 'research']
['years', 'births', 'by', 'year', 'deaths', 'by', 'year', 'years', 'music', 'films', 'by', 'year', 'history', 'years', 'film']
['popular', 'geology', 'current', 'research']
['years', 'births', 'by', 'year', 'deaths', 'by', 'year', 'years', 'music', 'films', 'by', 'year', 'history', 'years', 'film']
['popular', 'geology', 'current', 'research']
['years', 'births', 'by', 'year', 'deaths', 'by', 'year', 'years', 'music', 'films', 'by', 'year', 'history', 'years', 'film']
['popular', 'geology', 'current', 'research']
['years', 'births', 'by', 'year', 'deaths', 'by', 'year', 'years', 'music', 'films', 'by', 'year', 'history', 'years', 'film']
['popular', 'geology', 'current', 'research']
['years', 'births', 'by', 'year', 'deaths', 'by', 'year', 'years', 'music', 'films', 'by', 'year', 'history', 'years', 'film']
['paleontology', 'predation', 'nutrients', 'trophic', 'analysis', 'diet', 'metabolism']
['food', 'science', 'digestive', 'system']
['pa

['crystal', 'structure']
['quasiregular', 'polyhedra', 'platonic', 'solids', 'archimedean', 'solids', 'images', 'polyhedra', 'tessellation', 'kepler–poinsot', 'polyhedra', 'prismatoid', 'polyhedra', 'uniform', 'polyhedra', 'catalan', 'solids', 'johnson', 'solids', 'pyramids', 'bipyramids']
['crystal', 'structure']
['quasiregular', 'polyhedra', 'platonic', 'solids', 'archimedean', 'solids', 'images', 'polyhedra', 'tessellation', 'kepler–poinsot', 'polyhedra', 'prismatoid', 'polyhedra', 'uniform', 'polyhedra', 'catalan', 'solids', 'johnson', 'solids', 'pyramids', 'bipyramids']
['runoff', 'atmospheric', 'precipitation', 'hydrology', 'crystallization', 'geochemistry', 'sedimentation', 'salt', 'water', 'watersheds', 'storms', 'water']
['clouds']
['runoff', 'atmospheric', 'precipitation', 'hydrology', 'crystallization', 'geochemistry', 'sedimentation', 'salt', 'water', 'watersheds', 'storms', 'water']
['clouds']
['runoff', 'atmospheric', 'precipitation', 'hydrology', 'crystallization', 'geoc

['bogs', 'marshes', 'lacustrine', 'features', 'shore', 'features', 'spartina', 'alterniflora', 'conservation', 'geomorphology', 'vegetation', 'wilderness', 'areas', 'grasslands', 'swamps', 'ecology', 'fluvial', 'features']
['landforms', 'bodies', 'water']
['bogs', 'marshes', 'lacustrine', 'features', 'shore', 'features', 'spartina', 'alterniflora', 'conservation', 'geomorphology', 'vegetation', 'wilderness', 'areas', 'grasslands', 'swamps', 'ecology', 'fluvial', 'features']
['landforms', 'bodies', 'water']
['autochthons', 'allochthons', 'structural', 'geology', 'tectonics', 'erosion', 'features', 'overthrust', 'faults']
['microsoft', 'windows']
exception for autochthons
exception for allochthons
['autochthons', 'allochthons', 'structural', 'geology', 'tectonics', 'erosion', 'features', 'overthrust', 'faults']
['microsoft', 'windows']
['autochthons', 'allochthons', 'structural', 'geology', 'tectonics', 'erosion', 'features', 'overthrust', 'faults']
['microsoft', 'windows']
['autochthons

In [77]:

#saving the results in Thist2DBPEDIA_ok_res.csv
df.to_csv(path+'Thist2DBPEDIA_ok_resWithRT.csv', sep=';') 

# Considerations - lesson learnt for further attempts
Using the similarity on BT token does not seem very characterizing:
That is due to the design choices and data preparation:
- **choice 1**:  we split BT (e.g "Countries in Africa") in tokens (Countries, in, Africa) as "wmdistance" does not work on composed  text
     - should we use other pretrained model or build our own ? https://radimrehurek.com/gensim/wiki.html#preparing-the-corpus  
     - should we avoid to split the words in a flatten structure? 
     - Shall we use the vectors sum instead of splitting?
- **choice 2**: the similarity functions implements a naive and brute force approach
    - exceptions about not indexed word are repeated too often, should we check them in the similarity function outside the for?
    - is the right similarity? 
        - we might study and try other similarities provided by the same package GemSim
            - evaluate_word_pairs
            - Should we use document similarity? distance(d1, d2)¶ 
- **Data preparation**: 
    - there is more than a row for each link to be validated
    - BT are prefered label instead of URIs 
    - BT have repetition which are reevaluated during similarity calculation and create distortions on the score, can we remove them at the source?
- ** should we train word2vec differently?**    
    - **Is there any semantic embeddings of entities working with URIs?**
       - [Entity2vec](https://github.com/ot/entity2vec)
       - [Entity enbeddings](https://towardsdatascience.com/understanding-entity-embeddings-and-its-application-69e37ae1501d)
       - [An Introduction to Deep Learning for Tabular Data](https://www.fast.ai/2018/04/29/categorical-embeddings/)

# Learning the Model


https://academy.rapidminer.com/courses/creating-a-decision-tree-model